In [1]:
!pip install h3

DEPRECATION: Loading egg at /srv/conda/envs/notebook/lib/python3.11/site-packages/odp-0.0.1-py3.11.egg is deprecated. pip 24.3 will enforce this behaviour change. A possible replacement is to use pip for package installation. Discussion can be found at https://github.com/pypa/pip/issues/12330
  Using cached h3-3.7.7-cp311-cp311-manylinux_2_17_x86_64.manylinux2014_x86_64.whl.metadata (4.9 kB)
Using cached h3-3.7.7-cp311-cp311-manylinux_2_17_x86_64.manylinux2014_x86_64.whl (1.2 MB)


In [9]:
!pip install joblib

DEPRECATION: Loading egg at /srv/conda/envs/notebook/lib/python3.11/site-packages/odp-0.0.1-py3.11.egg is deprecated. pip 24.3 will enforce this behaviour change. A possible replacement is to use pip for package installation. Discussion can be found at https://github.com/pypa/pip/issues/12330


In [15]:
import numpy as np
import pandas as pd
import h3
import geopandas as gpd
from shapely.geometry import Polygon
import matplotlib.pyplot as plt
from tqdm import tqdm  # Import tqdm for progress bar
from joblib import Parallel, delayed
import pydeck as pdk

In [2]:
# Load the ocean polygons GeoJSON file
ocean_gdf = gpd.read_file('ne_10_ocean_geojson_simp.json')

# Check for invalid geometries
invalid_geometries = ocean_gdf[~ocean_gdf.is_valid]

if not invalid_geometries.empty:
    print(f"Found {len(invalid_geometries)} invalid geometries")

# Fix invalid geometries (attempt to make them valid)
ocean_gdf['geometry'] = ocean_gdf['geometry'].apply(lambda geom: geom.buffer(0) if not geom.is_valid else geom)

# Verify that all geometries are now valid
assert ocean_gdf.is_valid.all(), "There are still invalid geometries in the GeoJSON"


Found 1 invalid geometries


In [3]:
# Simplify the geometries with a tolerance value
# The tolerance value controls the degree of simplification; adjust it as needed
tolerance = 0.1  # Example tolerance, you can increase or decrease this based on your needs
gdf_simplified = ocean_gdf.copy()
gdf_simplified['geometry'] = ocean_gdf['geometry'].simplify(tolerance, preserve_topology=True)

In [4]:
# Save the simplified GeoJSON to a new file
simplified_geojson_file = 'ne_10_ocean_geojson_simplified.json'
gdf_simplified.to_file(simplified_geojson_file, driver='GeoJSON')

In [5]:
ocean_gdf = gdf_simplified.copy()

In [6]:
resolution=2

In [7]:
# Get the 122 base cells covering the globe
base_cells = h3.get_res0_indexes()

# Expand these base cells to the desired resolution
h3_indices = []
for base_cell in base_cells:
    h3_indices.extend(h3.uncompact([base_cell], resolution))

# Remove duplicates just in case (shouldn't be necessary, but it's safe)
h3_indices = list(set(h3_indices))

# Convert to DataFrame
unique_h3_indices = pd.DataFrame(h3_indices, columns=['h3_index'])

In [8]:
len(unique_h3_indices)

5882

In [9]:
# Function to classify an H3 hexagon
def classify_h3_hexagon(h3_index, ocean_gdf):
    # Get the polygon of the H3 hexagon
    h3_polygon = Polygon(h3.h3_to_geo_boundary(h3_index, geo_json=True))
    
    # Check if the H3 polygon is completely within ocean polygons
    if ocean_gdf.contains(h3_polygon).any():
        return "ocean"
    
    # Check if the H3 polygon intersects with any ocean polygons (for coastal)
    elif ocean_gdf.intersects(h3_polygon).any():
        return "coast"
    
    # If it's not in the ocean and not coastal, it must be land
    else:
        return "land"


In [10]:
# Define a parallel processing function
def parallel_classification(h3_index):
    return classify_h3_hexagon(h3_index, ocean_gdf)

# Use tqdm to provide a progress bar
tqdm.pandas(desc=f"Classifying H3 indices at resolution {resolution}")

# Apply the function in parallel
n_jobs = -1  # Use all available cores
unique_h3_indices['classification'] = Parallel(n_jobs=n_jobs)(
    delayed(parallel_classification)(x) for x in tqdm(unique_h3_indices['h3_index'])
)

100%|██████████| 5882/5882 [00:13<00:00, 420.30it/s]


In [ ]:
# Save the classification mapping to a CSV for future use
unique_h3_indices.to_csv(f'h3_classification_level_{resolution}.csv', index=False)

In [11]:
classification_h4 = pd.read_csv('h3_classification_level_4.csv')


In [12]:
# Define the function to classify H6 hexagons based on H4 classification
def classify_h6_from_h4(h4_index, ocean_gdf):
    # Get all H6 children of this H4 hexagon
    h6_children = h3.h3_to_children(h4_index, 6)
    
    # Check the classification of this H4 hexagon
    h4_classification = classification_h4.loc[classification_h4['h3_index'] == h4_index, 'classification'].values[0]
    
    if h4_classification in ['land', 'ocean']:
        # If H4 is entirely land or ocean, inherit this classification
        return [(h6, h4_classification) for h6 in h6_children]
    else:
        # If H4 is coast, classify each H6 hexagon individually
        return [(h6, classify_h3_hexagon(h6, ocean_gdf)) for h6 in h6_children]

# Define the parallel processing function
def parallel_classification(h4_index, ocean_gdf):
    return classify_h6_from_h4(h4_index, ocean_gdf)

In [13]:
# Create a list of H4 indices
h4_indices = classification_h4['h3_index'].tolist()


In [ ]:
#Use joblib's Parallel and delayed to process in parallel with a progress bar
n_jobs = -1  # Use all available cores
results = Parallel(n_jobs=n_jobs)(
    delayed(parallel_classification)(h4_index, ocean_gdf) for h4_index in tqdm(h4_indices)
)

In [16]:
# Flatten the list of results
flat_results = [item for sublist in results for item in sublist]

# Convert to DataFrame
df_h6 = pd.DataFrame(flat_results, columns=['h3_index', 'classification'])

# Save the results
df_h6.to_csv('h3_classification_level_6.csv', index=False)

In [52]:
input_filename = 'h3_classification_level_4.csv'
output_html = input_filename.replace('.csv', '.html')

In [53]:
# Load the classification CSV file (e.g., for resolution 2)
classification_df = pd.read_csv(input_filename)

In [54]:
classification_df

h3_index classification
0       845ca11ffffffff          ocean
1       84ae631ffffffff          ocean
2       84ec6a3ffffffff           land
3       8489903ffffffff          ocean
4       84c1a03ffffffff          ocean
...                 ...            ...
288117  844e1c7ffffffff          ocean
288118  84f32b1ffffffff          ocean
288119  8467b41ffffffff          ocean
288120  84ce65bffffffff          ocean
288121  8482683ffffffff          ocean

[288122 rows x 2 columns]

In [51]:
# Compute percentages of each classification
classification_counts = classification_df['classification'].value_counts()
total_hexagons = len(classification_df)

# Calculate percentages
classification_percentages = (classification_counts / total_hexagons) * 100

# Print the results
print("Percentage of each classification:")
for classification, percentage in classification_percentages.items():
    print(f"{classification.capitalize()}: {percentage:.2f}%")

Percentage of each classification:
Ocean: 59.15%
Coast: 20.79%
Land: 20.06%


In [46]:
# Map classifications to colors
classification_df['color'] = classification_df['classification'].map({
    'land': [0, 255, 0, 200],    # Green with some transparency
    'ocean': [0, 0, 255, 200],   # Blue with some transparency
    'coast': [255, 255, 255, 200]  # Yellow with some transparency
})

In [48]:
# Create the H3HexagonLayer
layer = pdk.Layer(
    'H3HexagonLayer',
    classification_df,
    get_hexagon='h3_index',        # H3 index field in your data
    get_fill_color='color',
    opacity=1,
    extruded=False,
    get_line_color=[32, 10, 58, 20],
    line_width_min_pixels=1,
    pickable=True,
    filled=True,
    stroked=True
)

# Create a Pydeck Layer
layer2 = pdk.Layer(
    'GeoJsonLayer',
    ocean_gdf,
    get_line_color='[0, 0, 0, 150]',
    get_fill_color='[0,0,0,0]',
    line_width_min_pixels=1,
)


# Set the initial view state
view = pdk.ViewState(
    latitude=55.0,  # Center latitude
    longitude=10.0, # Center longitude
    zoom=1,
    pitch=0
)

# Create a Pydeck Deck instance
deck = pdk.Deck(
    layers=[layer, layer2],
    initial_view_state=view,
    tooltip={"text": "{count}"},
    map_provider="mapbox", 
    map_style='mapbox://styles/oceandatafoundation/clwg6xklg00an01pcgmeufjxq', 
    api_keys={'mapbox': 'pk.eyJ1Ijoib2NlYW5kYXRhZm91bmRhdGlvbiIsImEiOiJjazk5bGxpNWkwYWU1M2Vya3hkcHh4czdrIn0.yf7kIiPfDNE7KP9_9wTN6A'}
)

# Display the map
deck

{
  "initialViewState": {
    "latitude": 55.0,
    "longitude": 10.0,
    "pitch": 0,
    "zoom": 1
  },
  "layers": [
    {
      "@@type": "H3HexagonLayer",
      "data": [
        {
          "classification": "ocean",
          "color": [
            0,
            0,
            255,
            200
          ],
          "h3_index": "823b27fffffffff"
        },
        {
          "classification": "land",
          "color": [
            0,
            255,
            0,
            200
          ],
          "h3_index": "823d57fffffffff"
        },
        {
          "classification": "coast",
          "color": [
            255,
            255,
            255,
            200
          ],
          "h3_index": "82be77fffffffff"
        },
        {
          "classification": "ocean",
          "color": [
            0,
            0,
            255,
            200
          ],
          "h3_index": "82a037fffffffff"
        },
        {
          "classification": "ocean",
          "color": [
            0,
            0,
            255,
            200
          ],
          "h3_index": "829f0ffffffffff"
        },
        {
          "classification": "ocean",
          "color": [
            0,
            0,
            255,
            200
          ],
          "h3_index": "82a427fffffffff"
        },
        {
          "classification": "land",
          "color": [
            0,
            255,
            0,
            200
          ],
          "h3_index": "82f2effffffffff"
        },
        {
          "classification": "land",
          "color": [
            0,
            255,
            0,
            200
          ],
          "h3_index": "826b77fffffffff"
        },
        {
          "classification": "ocean",
          "color": [
            0,
            0,
            255,
            200
          ],
          "h3_index": "825d9ffffffffff"
        },
        {
          "classification": "coast",
          "color": [
            255,
            255,
            255,
            200
          ],
          "h3_index": "820c17fffffffff"
        },
        {
          "classification": "ocean",
          "color": [
            0,
            0,
            255,
            200
          ],
          "h3_index": "825c37fffffffff"
        },
        {
          "classification": "coast",
          "color": [
            255,
            255,
            255,
            200
          ],
          "h3_index": "822b17fffffffff"
        },
        {
          "classification": "land",
          "color": [
            0,
            255,
            0,
            200
          ],
          "h3_index": "823ccffffffffff"
        },
        {
          "classification": "coast",
          "color": [
            255,
            255,
            255,
            200
          ],
          "h3_index": "820987fffffffff"
        },
        {
          "classification": "coast",
          "color": [
            255,
            255,
            255,
            200
          ],
          "h3_index": "820c37fffffffff"
        },
        {
          "classification": "ocean",
          "color": [
            0,
            0,
            255,
            200
          ],
          "h3_index": "82ae07fffffffff"
        },
        {
          "classification": "coast",
          "color": [
            255,
            255,
            255,
            200
          ],
          "h3_index": "8295a7fffffffff"
        },
        {
          "classification": "ocean",
          "color": [
            0,
            0,
            255,
            200
          ],
          "h3_index": "82e8effffffffff"
        },
        {
          "classification": "coast",
          "color": [
            255,
            255,
            255,
            200
          ],
          "h3_index": "829c1ffffffffff"
        },
        {
          "classification": "ocean",
          "color": [
            0,
            

In [49]:
deck.to_html(output_html, notebook_display=False)
